# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

#### Created by Silvia Huang, CFFS Data Analyst
****

## Part II: Data Cleaning

## Set up and Import Libraries

In [1]:
#pip install -r requirements.txt

In [2]:
import numpy as np
import pandas as pd
import pdpipe as pdp
import matplotlib.pyplot as plt
import glob
import os
import csv
from itertools import islice
from decimal import Decimal
import xml.etree.ElementTree as et
from xml.etree.ElementTree import parse
import openpyxl
import pytest
from datetime import datetime

C:\Users\smvan\anaconda3\lib\site-packages\pdpipe\col_generation.py:12: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [3]:
# Set the root path, change the the current working directory into the project folder
path = "C:/Users/smvan/CFFS-S23/CFFS-22-23"
# path = os.getcwd()
print(path)
os.chdir(path)

C:/Users/smvan/CFFS-S23/CFFS-22-23


In [4]:
# Enable reading data table in the scrolling window if you prefer
pd.set_option("display.max_rows", None, "display.max_columns", None)

***

## Import Preprocessed Datasets

In [5]:
# Read Items_List.csv
# Reading csv file: C:/Users/smvan/CFFS-S23/CFFS-22-23/data/preprocessed/Items_List.csv
Items = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Items_List.csv"))
Items.dtypes

ItemId             object
Description        object
CaseQty           float64
CaseUOM            object
PakQty            float64
PakUOM             object
InventoryGroup     object
dtype: object

In [6]:
# Display first 5 rows
Items.head()

ItemId                     Description  CaseQty CaseUOM  PakQty PakUOM  \
0   I-7631                  5 SPICE POWDER      1.0      ea     1.0     lb   
1   I-2352   9"X6" 1-COMPARTMENT CLAMSHELL    200.0      CT     1.0     CT   
2  I-57481     AHA WATER SP BLUEB POM PET      24.0    each     1.0   each   
3  I-57484  AHA WATER SP PEACH HONEY PET       24.0    each     1.0   each   
4  I-56025  AHA WATER SP WATERMLN LIME PET     24.0    each     1.0   each   

  InventoryGroup  
0         SPICES  
1    DISPOSABLES  
2       BEVERAGE  
3       BEVERAGE  
4       BEVERAGE

In [7]:
# There are 486 rows and 7 columns
Items.shape

(1399, 7)

In [8]:
# Read Ingredients_List.csv
Ingredients = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Ingredients_List.csv"))
Ingredients.dtypes

IngredientId     object
Qty             float64
Uom              object
Conversion      float64
InvFactor       float64
Recipe           object
dtype: object

In [9]:
# Display first 5 rows
Ingredients.head()

IngredientId   Qty Uom  Conversion  InvFactor   Recipe
0       P-9857   5.0  Kg         1.0     1.1111  P-10112
1      P-48933   1.0  Kg         1.0     1.0000  P-10113
2       I-4626  16.0  CT         1.0     2.6667  P-10115
3       P-9755   1.0  lb         1.0     1.0000  P-10119
4      P-18746   1.0  Kg         1.0     1.0000  P-10241

In [10]:
# There are 3278 rows and 6 columns
Ingredients.shape

(12690, 6)

In [11]:
# Read Preps_List.csv
Preps = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Preps_List.csv"))
Preps.dtypes

PrepId             object
Description        object
PakQty            float64
PakUOM             object
InventoryGroup     object
dtype: object

In [12]:
# Display first 5 rows
Preps.head()

PrepId                   Description  PakQty PakUOM InventoryGroup
0  P-61901            ADD|Gomae|broccoli   120.0      g            NaN
1  P-57304  ADD|Pasta accoutresmonts| +2   150.0      g            NaN
2  P-47540                 Alfredo- 2018    15.0      L           PREP
3  P-46066            Almond Milk Yeild    900.0     ml            NaN
4  P-49557           ALMOND UNSALTED CUP     1.0    cup           PREP

In [13]:
# There are 546 rows and 5 columns
Preps.shape

(1427, 5)

In [14]:
# Read Product_List.csv that was created from 1_data preprocessing
Products = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Products_List.csv"))
Products.dtypes

ProdId         object
Description    object
SalesGroup     object
dtype: object

In [15]:
# Display first 5 rows
Products.head()

ProdId               Description    SalesGroup
0  R-44735        ADD|Arugula|Omelet       ADD ONS
1  R-16241            ADD|Beef Patty  GV GRILL DAY
2  R-44780  ADD|Condiment House Made       ADD ONS
3  R-13180              ADD|Crackers       ADD ONS
4  R-44739   ADD|Creamed Spin|Omelet       ADD ONS

In [16]:
# There are 223 rows and 3 columns
Products.shape

(1891, 3)

In [17]:
# Read Coversions_List.csv that was created from 1_data preprocessing
Conversions = pd.read_csv(os.path.join(os.getcwd(), "data", "preprocessed", "Conversions_List.csv"))
Conversions.dtypes

ConversionId       object
Multiplier        float64
ConvertFromQty    float64
ConvertFromUom     object
ConvertToQty      float64
ConvertToUom       object
dtype: object

In [18]:
# Display first 5 rows
Conversions.head()

ConversionId  Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty  \
0          NaN    1.000000             1.0            XXX          1.00   
1          NaN    0.877193             1.0          1.14L          1.14   
2          NaN    0.666667             1.0           1.5L          1.50   
3          NaN    0.571429             1.0         1.75 L          1.75   
4          NaN    0.500000             1.0             2L          2.00   

  ConvertToUom  
0            L  
1            L  
2            L  
3            L  
4            L

In [19]:
# There are 270 rows and 6 columns
Conversions.shape

(454, 6)

***
## Update Conversion List

In [20]:
# Add the specific conversion info from the newly-processed data to a unit conversion database
Update_Conv = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "update", "Conv_UpdateConv.csv"))
Update_Conv

ConversionId  Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty  \
0         I-1028    0.008333           1.000             CT      120.0000   
1         I-1034    0.008333           1.000             CT      120.0000   
2         I-1035    0.010000           1.000             CT      100.0000   
3        I-10605    0.008850           1.000             CT      113.0000   
4         I-1126    0.006667           1.000             CT      150.0000   
5         I-1127    0.006667           1.000             CT      150.0000   
6         I-1141    0.013333           1.000             CT       75.0000   
7         I-1143    0.013333           1.000             CT       75.0000   
8        I-11519    0.020000           1.000            bag       50.0000   
9         I-1152    0.013333           1.000             CT       75.0000   
10       I-11842    0.002203           1.000           LOAF      454.0000   
11        I-1207    0.008333           1.000             CT      120.0000   
12        I-1223    0.000100           1.000             CT    10000.0000   
13        I-1232    0.020000           1.000          slice       50.0000   
14        I-1252    0.000250           1.000             CT     4000.0000   
15        I-1254    0.004167           0.500             CT      120.0000   
16        I-1257    0.008333           1.000             CT      120.0000   
17        I-1273    0.002203           1.000           LOAF      454.0000   
18       I-13004    0.002203           1.000             CT      454.0000   
19       I-15032    0.002203           1.000           LOAF      454.0000   
20       I-15358    0.013333           1.000             ea       75.0000   
21       I-17615    0.071429           1.000          slice       14.0000   
22       I-17617    0.071429           1.000          slice       14.0000   
23       I-17686    0.013333           1.000             ea       75.0000   
24       I-18089    0.008333           1.000             ea      120.0000   
25       I-18915    0.033333           1.000             ea       30.0000   
26       I-19735    0.008333           1.000             CT      120.0000   
27        I-2159    0.020000           1.000             CT       50.0000   
28        I-2281    0.000117           0.076           650G      650.0000   
29        I-2306    0.050000           1.000          slice       20.0000   
30        I-2310    0.050000           1.000          slice       20.0000   
31       I-24227    0.002203           1.000           LOAF      454.0000   
32        I-2586    0.008333           1.000             CT      120.0000   
33        I-2669    0.000862           0.125            PIE      145.0000   
34       I-28899    0.040000           1.000           each       25.0000   
35       I-28904    0.033333           1.000           each       30.0000   
36       I-28907    0.025000           1.000           each       40.0000   
37       I-28920    0.005882           1.000           each      170.0000   
38       I-29663    0.036364           1.000             ea       27.5000   
39       I-29665    0.025000           1.000           each       40.0000   
40       I-29688    0.008333           1.000             ea      120.0000   
41       I-30178    0.008333           1.000          SHEET      120.0000   
42        I-3103    0.033333           1.000             CT       30.0000   
43        I-3143    0.000352           1.000            can     2840.0000   
44       I-32258    0.020000           1.000             ea       50.0000   
45       I-32263    0.033333           1.000             ea       30.0000   
46       I-32268    0.020000           1.000             ea       50.0000   
47        I-3387    0.001000           1.000              L     1000.0000   
48        I-3676    0.000352           1.000         LG CAN     2840.0000   
49        I-3688    0.008333           1.000             CT      120.0000   
50        I-3738    0.003030           1.000          330ML      330.0000   


In [21]:
# return dataframe with null values
# There are no null values
subset_conv = Update_Conv[Update_Conv["Multiplier"].isna()]
subset_conv

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [22]:
# takes a data frame and assigns a new column called Multiplier to the dataframe
# uses iterrows() to iterate through the rows.Then subset_conv will have a new column named Multiplier with the computed values.
def assign_multiplier(df):
    for ind, row in df.iterrows():
        df.loc[ind, "Multiplier"] = row["ConvertFromQty"] / row["ConvertToQty"]
        
assign_multiplier(subset_conv)

# May 8th change: We want to 
assign_multiplier(Update_Conv)
#subset_conv

In [24]:
# convert dataframe to csv file
Update_Conv = pd.concat([Update_Conv, subset_conv], axis=0)
Update_Conv.to_csv("data/cleaning/update/Conv_UpdateConv.csv", index=False)

In [25]:
# retrieves the value in the 'ConversionId' column using Update_Conv.loc[index, 'ConversionId'] 
# and assigns it to the variable Id. 

# row: a Series (1-d array in pandas) You can access the individual values of the row using the column headers as keys to the
# like row['column_name'].

# if the IDs of Update_Conv are the same IDs as Conversions then we drop it from the Conversions dataframe

for index, row in Update_Conv.iterrows():
    Id = Update_Conv.loc[index, 'ConversionId']
    Conversions.drop(Conversions[Conversions['ConversionId'] == Id].index, inplace = True)

In [26]:
# combine two data frames, reset the index and remove any duplicates in the concatenated data frame, 
# and return the resulting data frame.

# Added comments below on May 8th

# frames variable is created as a list of two DataFrames, Conversions and Update_Conv.
# pd.concat() function is used to concatenate the two DataFrames vertically (i.e., stack one on top of the other). 

# drop_duplicates() method is used to remove any duplicate rows from the concatenated DataFrame based on all columns. 
# The resulting DataFrame has only unique rows.

# The resulting DataFrame is assigned back to the variable Conversions,

# drop = True ensures that the old index is not added as a new column to the dataframe 
# inplace=False parameter ensures that a new DataFrame is returned rather than modifying 
# the original Conversions DataFrame in place.

frames = [Conversions, Update_Conv]
Conversions = pd.concat(frames).reset_index(drop=True, inplace=False).drop_duplicates()

In [27]:
Conversions

ConversionId   Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty  \
0            NaN     1.000000          1.0000            XXX        1.0000   
1            NaN     0.877193          1.0000          1.14L        1.1400   
2            NaN     0.666667          1.0000           1.5L        1.5000   
3            NaN     0.571429          1.0000         1.75 L        1.7500   
4            NaN     0.500000          1.0000             2L        2.0000   
5            NaN     0.250000          1.0000             4L        4.0000   
6            NaN     0.083333          1.0000           FOOT       12.0000   
7            NaN     0.062500          1.0000            16L       16.0000   
8            NaN     0.059172          1.0000         1/2LTR       16.9000   
9            NaN     0.039370          1.0000          750ML       25.4000   
10           NaN     0.033333          1.0000        KEG 30L       30.0000   
11           NaN     0.025974          1.0000         1140ml       38.5000   
12           NaN     0.025000          1.0000        full in       40.0000   
13           NaN     0.020000          1.0000        KEG 50L       50.0000   
14           NaN     0.017065          1.0000        KEG 59L       58.6000   
15           NaN     0.016667          1.0000           HOUR       60.0000   
16           NaN     0.002000          1.0000          500ML      500.0000   
17           NaN     0.001538          1.0000          650ML      650.0000   
18           NaN     0.001515          1.0000          660ML      660.0000   
19           NaN     0.001429          1.0000          700ML      700.0000   
20           NaN     0.001408          1.0000          710ml      710.0000   
21           NaN     0.001333          1.0000          750ML      750.0000   
22           NaN     0.000592          1.0000         keg50L     1690.0000   
23           NaN     0.000504          1.0000         keg59L     1984.0000   
24           NaN     2.000000          2.0000            cup        1.0000   
25           NaN     2.000000          2.0000             pt        1.0000   
26           NaN     2.000000          2.0000           Tbsp        1.0000   
27           NaN     3.000000          3.0000            tsp        1.0000   
28           NaN     4.000000          4.0000             qt        1.0000   
29           NaN     8.000000          8.0000          fl oz        1.0000   
30           NaN    16.000000         16.0000             oz        1.0000   
31           NaN    28.349500         28.3495              g        1.0000   
32           NaN    29.573500         29.5735             ml        1.0000   
33           NaN    35.211268        100.0000          fl oz        2.8400   
34           NaN  1000.000000       1000.0000              g        1.0000   
35           NaN  1000.000000       1000.0000             mg        1.0000   
36           NaN  1000.000000       1000.0000             ml        1.0000   
37        I-1041     1.000000          1.0000             CT        1.0000   
38        I-1100     1.000000          1.0000             CT        1.0000   
39        I-1122     0.014286          1.0000             CT       70.0000   
40        I-1197     0.013333          1.0000             CT       75.0000   
41        I-1274     1.000000          1.0000           LOAF        1.0000   
42        I-1750     1.000000          1.0000          355ML        1.0000   
43        I-1790     0.032258          1.0000          fl oz       31.0000   
44        I-1790     0.005000          1.0000            PTN      200.0000   
45        I-1790     0.004032          1.0000            cup      248.0000   
46        I-1813     0.032787          1.0000          fl oz       30.5000   
47        I-1813     0.004098          1.0000            cup      244.0000   
48        I-1814     0.032787          1.0000          fl oz       30.5000   
49        I-1814     0.004098          1.0000            cup      244.0000   
50        I-1820     0.032

In [28]:
# Convert the DataFrame: Conversions into a csv file called Conversions_Added.csv
path = os.path.join(os.getcwd(), "data", "cleaning", "Conversions_Added.csv")
Conversions.to_csv(path, index = False, header = True)

### Create Unit Converter

In [29]:
# Import standard unit conversion information and construct a dataframe
Std_Unit = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "standard_conversions.csv"))
Std_Unit.head()

Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty ConvertToUom
0     4.92890               1            tsp       4.92890           ml
1    14.78700               1           Tbsp      14.78700           ml
2   946.35000               1             qt     946.35000           ml
3   473.17625               1             pt     473.17625           ml
4    28.34950               1             oz      28.34950            g

In [30]:
# Seperate uoms that converted to 'ml' or 'g'
# Below we create 2 lists. 
# list_unit contains list of unit of measurements that are being converted to milliliters 
# solid_unit contains a list of unit of measurements that are being converted to grams
# tolist() converts a Pandas Series or an array to a python list. 

liquid_unit = Std_Unit.loc[Std_Unit['ConvertToUom'] == 'ml', 'ConvertFromUom'].tolist()
solid_unit = Std_Unit.loc[Std_Unit['ConvertToUom'] == 'g', 'ConvertFromUom'].tolist()

In [31]:
# Construct a standard unit converter
def std_converter(qty, uom):
    if uom in Std_Unit['ConvertFromUom'].tolist():
        multiplier = Std_Unit.loc[Std_Unit['ConvertFromUom'] == uom, 'Multiplier']
        Qty = float(qty)*float(multiplier)
        Uom = Std_Unit.loc[Std_Unit['ConvertFromUom'] == uom, 'ConvertToUom'].values[0]
    else:
        Qty = qty
        Uom = uom
    return (Qty, Uom)

In [32]:
# Convert pounds to grams
std_converter(0.25,'lb')

(113.398, 'g')

In [33]:
# Test the std_converter
assert std_converter(0.25,'lb') == (113.398, 'g')

In [34]:
# Construct a unit converter for specific ingredients

# After this line below, spc_cov contains only the non-empty values from the 'ConversionId' column of the Conversions DataFrame.
spc_cov = list(filter(None, Conversions['ConversionId'].tolist()))


# Comments for spc_converter:
# The function checks if ingredient is in the liquid_unit or solid_unit lists. If so, it calls std_converter(qty, uom) to 
# convert the quantity and UOM to a standardized unit.

# If uom is not in liquid_unit or solid_unit it checks if ingre is in spc_cov, if it is and the ConvertToUom is equal to grams 
# then the function applies the factor to the qty argument to convert it to the standardized unit, and returns the result as
# a tuple containing the converted quantity and uom. If no conversion found, then it calls std_converter(qty, uom)

# If uom not in liquid_unit or solid_unit and if ingre is not in spc_cov then the function calls std_converter(qty, uom)

def spc_converter(ingre, qty, uom):
    if uom in liquid_unit + solid_unit:
        return std_converter(qty, uom)
    elif ingre in spc_cov:
        conversion = Conversions.loc[(Conversions['ConversionId'] == ingre) & (Conversions['ConvertFromUom'] == uom)
                                    & (Conversions['ConvertToUom'] == 'g')]
        multiplier = conversion['Multiplier']
        if multiplier.empty:
            return std_converter(qty, uom)
        else: 
            Qty = float(qty)/float(multiplier)
            Uom = conversion['ConvertToUom'].values[0]
            return (Qty, Uom)
    else:
        return std_converter(qty, uom)

In [35]:
spc_cov

[nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 nan,
 'I-1041',
 'I-1100',
 'I-1122',
 'I-1197',
 'I-1274',
 'I-1750',
 'I-1790',
 'I-1790',
 'I-1790',
 'I-1813',
 'I-1813',
 'I-1814',
 'I-1814',
 'I-1820',
 'I-1820',
 'I-1821',
 'I-1821',
 'I-1827',
 'I-1827',
 'I-2158',
 'I-2174',
 'I-2188',
 'I-2208',
 'I-2208',
 'I-2217',
 'I-2217',
 'I-2218',
 'I-2218',
 'I-2218',
 'I-2220',
 'I-2220',
 'I-2220',
 'I-2221',
 'I-2221',
 'I-2221',
 'I-2251',
 'I-2251',
 'I-2251',
 'I-2254',
 'I-2254',
 'I-2267',
 'I-2319',
 'I-2596',
 'I-2654',
 'I-2866',
 'I-2903',
 'I-2903',
 'I-2903',
 'I-2949',
 'I-3080',
 'I-3140',
 'I-3140',
 'I-3141',
 'I-3144',
 'I-3144',
 'I-3144',
 'I-3145',
 'I-3145',
 'I-3146',
 'I-3146',
 'I-3149',
 'I-3159',
 'I-3223',
 'I-3223',
 'I-3224',
 'I-3224',
 'I-3225',
 'I-3225',
 'I-3237',
 'I-3283',
 'I-3283

In [36]:
# spc_cov2 is the same as spc_cov but without null values labelled as "nan" in the list
import math
spc_cov2 = [item for item in spc_cov if not(pd.isnull(item)) == True]
spc_cov2

['I-1041',
 'I-1100',
 'I-1122',
 'I-1197',
 'I-1274',
 'I-1750',
 'I-1790',
 'I-1790',
 'I-1790',
 'I-1813',
 'I-1813',
 'I-1814',
 'I-1814',
 'I-1820',
 'I-1820',
 'I-1821',
 'I-1821',
 'I-1827',
 'I-1827',
 'I-2158',
 'I-2174',
 'I-2188',
 'I-2208',
 'I-2208',
 'I-2217',
 'I-2217',
 'I-2218',
 'I-2218',
 'I-2218',
 'I-2220',
 'I-2220',
 'I-2220',
 'I-2221',
 'I-2221',
 'I-2221',
 'I-2251',
 'I-2251',
 'I-2251',
 'I-2254',
 'I-2254',
 'I-2267',
 'I-2319',
 'I-2596',
 'I-2654',
 'I-2866',
 'I-2903',
 'I-2903',
 'I-2903',
 'I-2949',
 'I-3080',
 'I-3140',
 'I-3140',
 'I-3141',
 'I-3144',
 'I-3144',
 'I-3144',
 'I-3145',
 'I-3145',
 'I-3146',
 'I-3146',
 'I-3149',
 'I-3159',
 'I-3223',
 'I-3223',
 'I-3224',
 'I-3224',
 'I-3225',
 'I-3225',
 'I-3237',
 'I-3283',
 'I-3283',
 'I-3284',
 'I-3284',
 'I-3284',
 'I-3321',
 'I-3327',
 'I-3327',
 'I-3348',
 'I-3365',
 'I-3365',
 'I-3367',
 'I-3370',
 'I-3386',
 'I-3386',
 'I-3386',
 'I-3388',
 'I-3388',
 'I-3388',
 'I-3389',
 'I-3389',
 'I-3389',

In [37]:
# Here we pass in the ingredient (I-1120) the quantity of the ingredient (1) and the unit of measurement: CT -> count
# This gives us the number of grams of that ingredient
spc_converter('I-1120', 1, 'CT')

(1, 'CT')

In [38]:
# Identify the ones that are not in the conversion list 

In [39]:
Conversions.loc[Conversions["ConversionId"] == "I-14190"]

ConversionId  Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty  \
751      I-14190    0.001667             1.0           LOAF         600.0   

    ConvertToUom  
751            g

In [40]:
c_list = Conversions["ConversionId"].unique()
"I-68700" in c_list

True

In [41]:
spc_converter("I-14190", 1, "LOAF")

(600.0, 'g')

In [42]:
spc_converter('I-47530', 7, 'ea')

(7, 'ea')

In [43]:
# Test the spc_converter
# spc_converter('I-1120', 1, 'CT')
#assert spc_converter('I-1120', 1, 'CT') == (134.99995275001655, 'g')

***
## Items with Non-standard Units

In [44]:
Ingredients

IngredientId        Qty     Uom   Conversion   InvFactor   Recipe
0           P-9857      5.000      Kg     1.000000      1.1111  P-10112
1          P-48933      1.000      Kg     1.000000      1.0000  P-10113
2           I-4626     16.000      CT     1.000000      2.6667  P-10115
3           P-9755      1.000      lb     1.000000      1.0000  P-10119
4          P-18746      1.000      Kg     1.000000      1.0000  P-10241
5          P-18746      1.000      Kg     1.000000      1.0000  P-10242
6          P-18746      1.000      Kg     1.000000      1.0000  P-10243
7           I-3388    100.000      ml     0.001000      2.5000  P-10264
8          I-37842      9.070      Kg     1.000000      0.2268  P-10264
9           I-5983     40.000       L     1.000000      1.0000  P-10264
10          I-3388      1.000       L     1.000000      0.3058  P-10496
11          I-4658      2.270      Kg     2.204620      0.6942  P-10496
12          I-1813     30.000      ml     0.033814      9.3750  P-10502
13          I-6026     15.000       g     1.000000      4.6875  P-10502
14         I-60772      3.000       L     1.000000      0.9375  P-10502
15         P-41466    200.000       g     1.000000     62.5000  P-10502
16          P-6605    100.000       g     0.001000     31.2500  P-10502
17         P-45879      7.500      Kg     1.000000      1.8750  P-10873
18         I-12176      4.000       g     0.001000      0.3636  P-12112
19          I-1813    400.000      ml     0.033814     36.3636  P-12112
20          I-3337      4.000       L     1.000000      0.3636  P-12112
21          I-3387    100.000      ml     0.001000      9.0909  P-12112
22          I-3447    199.000      ml     1.000000     18.0909  P-12112
23          I-3507      6.000       L     1.000000      0.5455  P-12112
24          I-3639     30.000       g     1.000000      2.7273  P-12112
25          I-3642      4.000       g     1.000000      0.3636  P-12112
26          I-3658    350.000       g     0.001000     31.8182  P-12112
27         I-47774    200.000      ml     0.001000     18.1818  P-12112
28         I-13327      0.750     pak     1.000000      0.0125  P-12392
29          I-1559     15.000      ml     0.001000      0.2500  P-12392
30          I-1561     15.000      ml     0.001000      0.2500  P-12392
31          I-1564     15.000      ml     0.001000      0.2500  P-12392
32          I-2217      3.000      ml     0.001000      0.0500  P-12392
33          I-2501      0.250     pak     1.000000      0.0042  P-12392
34         I-65799      3.000      ml     1.000000      0.0500  P-12392
35         I-12176     10.000       g     0.001000      0.0952  P-12421
36          I-2911      5.000       g     0.001000      0.0476  P-12421
37          I-3629      5.000       g     0.035274      0.0476  P-12421
38          I-3630      5.000       g     0.035274      0.0476  P-12421
39          I-3640     75.000       g     1.000000      0.7143  P-12421
40          I-3642      5.000       g     1.000000      0.0476  P-12421
41         I-10871      2.000      lb     1.000000      0.1000  P-12427
42          I-3387     74.000      ml     0.001000      3.7000  P-12427
43          I-3435      0.500       L     1.000000      0.0250  P-12427
44          I-3619      5.000       g     1.000000      0.2500  P-12427
45          I-3649     20.000       g     1.000000      1.0000  P-12427
46          I-4381      2.000      lb     1.000000      0.1000  P-12427
47          I-4599      1.000    HEAD     1.000000      0.0500  P-12427
48          I-4847      1.000      oz     0.062500      0.0500  P-12427
49          I-4919      1.000      oz     0.062500      0.0500  P-12427
50          I-5983     35.000       L     1.000000      1.7500  P-12427
51          I-6781     20.000      Kg     1.000000      1.0000  P-12427
52          I-7061      2.000       L     1.000000      0.1000  P-12427
53          I-9662     40.000      lb     0.453592      2.0000  P-12427
54          I-1468      0.250   fl oz     1.00

In [45]:
Items

ItemId                     Description   CaseQty  CaseUOM    PakQty  \
0      I-7631                  5 SPICE POWDER      1.00       ea     1.000   
1      I-2352   9"X6" 1-COMPARTMENT CLAMSHELL    200.00       CT     1.000   
2     I-57481     AHA WATER SP BLUEB POM PET      24.00     each     1.000   
3     I-57484  AHA WATER SP PEACH HONEY PET       24.00     each     1.000   
4     I-56025  AHA WATER SP WATERMLN LIME PET     24.00     each     1.000   
5     I-43851                      AJWAIN 5LB      5.00       lb   454.000   
6      I-3617         ALLSPICE GROUND SHAKER       8.00     each   454.000   
7      I-1852           ALMOND BEV - ORIGINAL     24.00       CT     1.000   
8     I-61295       ALMOND BREEZE CHOC 240 ML     24.00       CT     1.000   
9     I-61294  ALMOND BREEZE VAN UNSWT 240 ML     24.00       CT     1.000   
10    I-44059                  ALMOND BUTTER*     10.00       Kg     1.000   
11    I-12157         ALMOND CHOC*TETRA 250Ml     18.00     each   236.000   
12    I-13970         ALMOND ORIG TETRA 250ML     24.00       ea     1.000   
13    I-40957          ALMOND SLICED*BLANCHED      1.00      5KG  5000.000   
14    I-43854                   AMCHUR POWDER      5.00       lb   454.000   
15    I-43652                    ANCHO CHILLI      1.20       Kg     1.000   
16     I-2852                   ANCHO POWDER       1.00      pak   227.000   
17     I-2853                ANCHOVIES FILLET      1.70       Kg     1.000   
18     I-6924                    ANISE (36CT)      3.00       CT     1.000   
19    I-11181                ANISE STAR WHOLE      8.00     each   240.000   
20     I-4255  APPLES CA AMBROSIA F/XF 100 CT    100.00       CT     1.000   
21    I-29389            APPLES DICED IQF FRZ      1.00      bag    18.180   
22     I-4249         APPLES FUJI F/XF 113 CT    113.00       CT     1.000   
23     I-4456                  APPLES FUJI US     64.00       CT     1.000   
24     I-6775              APPLES GALA ROYAL     100.00       CT     1.000   
25     I-4461            APPLES GALA ROYAL BC    100.00       CT     1.000   
26     I-4458       APPLES GOLDEN DELICIOUSUS    113.00       CT     1.000   
27     I-4970  APPLES GRANN SMITH SLCD GRDE A      2.00      bag     2.500   
28     I-4271            APPLES GRANNY SMITH     113.00       ea     1.000   
29    I-13253        APPLES GRANNY SMITH 88CT     88.00       CT     1.000   
30     I-8042  APPLES GRANNY SMITH US  113 CT      1.00       cs   113.000   
31     I-4459            APPLES HONEYCRISP BC     88.00       CT     1.000   
32     I-4460              APPLES MACINTOSHBC      5.00       lb     3.000   
33    I-13225      APPLES RED DELICIOUS 113CT      1.00       cs   113.000   
34    I-18918               APPLES RED SLICES     12.00       lb     1.000   
35     I-4462             APPLES SPARTANK39BC     39.00       lb     1.000   
36     I-7957         APRICOTS DRIED TFC BULK     12.00      pak     0.450   
37     I-4971     ARTICHOKE 1/4 SALAD CUT TFC      6.00   LG CAN     2.500   
38     I-4465            ASPARAGUS (LARGE) MX     11.00       lb     1.000   
39     I-4473               AVOCADO (20CT) MX     20.00       CT     1.000   
40     I-4472                      AVOCADO MX     20.00       CT     1.000   
41     I-4973             AVOCADO PULP*CHUNKY      6.00     each   907.185   
42    I-65741      BACON 2.5MM NATURALLY SMKD      5.00       Kg     1.000   
43    I-27410        BACON 3MM NATURALLY SMKD      5.00       Kg     1.000   
44    I-62928           BAGEL EVERYTHING*SLCD     12.00      pak     6.000   
45    I-63697            BAGEL MULTIGRAIN 4OZ     12.00      bag     6.000   
46     I-1252         BAGEL PLAIN  SLICED 4OZ     72.00       CT     1.000   
47    I-19178     BAGEL PLAIN G/FREE FZN (S0)      6.00      bag     5.000   
48     I-1286      BAGEL WHOLE WHEAT (6 PACK)      6.00       CT     1.000   
49     I-1207                BAGUETTE FRENCH      24.00     each     1.000   
50    I-18089                

In [46]:
# Filter out the items whose unit information is unknown 

# We find the column names
col_names = list(Ingredients.columns.values)

# Create a Items_Nonstd list
Items_Nonstd = []

# If the unit of measurement is not grams or ml and ingredient id starts with I and the ingredient is not in ConversionId column of Conversions 
# then we add it to Items_Nonstd list
for index, row in Ingredients.iterrows():
    Ingre = Ingredients.loc[index,'IngredientId']
    Uom = Ingredients.loc[index,'Uom']
    if Uom not in ['g', 'ml'] and Uom not in liquid_unit + solid_unit and Ingre.startswith('I') and Ingre not in Conversions["ConversionId"].tolist():
        Dict = {}
        Dict.update(dict(row))
        Items_Nonstd.append(Dict)

# Create a DataFrame from Items_Nonstd list
Items_Nonstd = pd.DataFrame(Items_Nonstd, columns = col_names)
# Remove duplicate ingredients of the same properties so that Items_Nonstd has only unique rows. 
Items_Nonstd.drop_duplicates(subset=['IngredientId'], inplace=True,)
Items_Nonstd

IngredientId     Qty     Uom  Conversion  InvFactor   Recipe
0        I-13327   0.750     pak         1.0     0.0125  P-12392
1         I-2501   0.250     pak         1.0     0.0042  P-12392
2        I-17680   0.200     bag         1.0     0.0333  P-14076
4        I-19633   1.000     pak         1.0     0.3333  P-23837
5        I-17151   5.000      CT         1.0     0.5000  P-28369
6        I-29427   0.333      ea         1.0     0.3330  P-33780
7        I-29442   0.333      ea         1.0     0.3330  P-33780
8        I-29443   0.333      ea         1.0     0.3330  P-33780
9        I-29436   0.333      ea         1.0     0.3330  P-38127
10       I-29437   0.333      ea         1.0     0.3330  P-38127
11       I-29438   0.333      ea         1.0     0.3330  P-38127
12        I-1263   0.090      CT         1.0     0.0900  P-38170
13       I-25119   1.000      ea         1.0     1.0000  P-38172
14       I-25121   1.000      ea         1.0     1.0000  P-42552
21        I-4947   1.000      CT         1.0     0.0080  P-45048
22        I-1852   1.000      CT         1.0     0.0011  P-46066
23       I-32323  30.000      ea         1.0     1.0000  P-46075
24        I-1047  12.000      CT         1.0     1.0000  P-46861
25       I-17571   1.000     DOZ         1.0     0.0833  P-46877
26       I-11854   1.000      CT         1.0     0.5000  P-47362
27       I-47759   1.000      ea         1.0     1.0000  P-47805
28       I-1079p   1.000      CT         1.0     1.0000  P-47859
29       I-1165p   1.000      CT         1.0     1.0000  P-47859
30       I-43547   1.000    each         1.0     1.0000  P-47859
32       I-31492   1.000      ea         1.0     1.0000  P-48485
33       I-16216   1.000   slice         1.0     1.0000  P-50510
34        I-7055   1.000   SHEET         1.0     0.0313  P-50725
35        I-7619   2.000      ea         1.0     1.0000  P-51225
37        I-9834   2.000      CT         1.0     0.2500  P-53318
38       I-11362   4.000      CT         1.0     0.1818  P-56119
39       I-19178  30.000      CT         1.0     1.3636  P-56119
40       I-64876   1.000    each         1.0     0.0083  P-64878
41       I-28914   3.000    each         1.0     3.0000  P-65742
42       I-68699   1.000    each         1.0     1.1765  P-69444
43        I-1051   0.042   SHEET         1.0     0.0420  P-69719
44        I-1060   0.042    CAKE         1.0     0.0420  P-69720
45       I-16007   0.042   SHEET         1.0     0.0420  P-69723
46        I-1149   5.000      CT         1.0     0.4167  P-70079
47       I-50577   0.010  Dollar         1.0     0.0005   P-7438
48       I-12123   0.500     PTN         1.0     1.0000  R-12397
49        I-1782   0.500     PTN         1.0     1.0000  R-12397
50       I-29232   1.000      ea         1.0     1.0000  R-13159
51       I-29689   1.000      ea         1.0     1.0000  R-13161
52       I-28412   1.000      ea         1.0     1.0000  R-13162
53       I-29699   0.333      ea         1.0     1.0000  R-13163
54       I-29700   0.333      ea         1.0     1.0000  R-13163
55       I-62928   1.000      ea         1.0     1.0000  R-13164
56        I-2116   0.250     PTN         1.0     1.0000  R-13165
57        I-2118   0.750     PTN         1.0     1.0000  R-13165
58        I-2773   1.000      CT         1.0     1.0000  R-13166
59       I-19501   0.125      ea         1.0     1.0000  R-13172
60       I-19502   0.125      ea         1.0     1.0000  R-13172
61       I-19503   0.125      ea         1.0     1.0000  R-13172
62       I-19504   0.125      ea         1.0     1.0000  R-13172
63        I-3323   0.167     PTN         1.0     1.0000  R-13177
64        I-3324   0.167     PTN         1.0     1.0000  R-13177
65        I-3325   0.167     PTN         1.0     1.0000  R-13177
66        I-3326   0.167     PTN         1.0     1.0000  R-13177
67        I-3441   0.167     PTN         1.0     1.0000  R-13177
68        I-2774   1.000      CT         1.0     1.0000  R-13178
69       I-47962   0.600   slice       

In [47]:
# Assigning a Description column to the Items_Nonstd    
    
# for index, row in Items_Nonstd.iterrows():
#     idx = row['IngredientId']
#     descrp = Items.loc[Items['ItemId'] == idx, 'Description'].values[0]
#     Items_Nonstd.loc[index, 'Description'] = descrp


# CHANGE AUG 3:
for index, row in Items_Nonstd.iterrows():
    idx = row['IngredientId']
    filtered_items = Items.loc[Items['ItemId'] == idx, 'Description']
    if not filtered_items.empty:
        descrp = filtered_items.values[0]
        Items_Nonstd.loc[index, 'Description'] = descrp
    else:
        # Handle the case when there is no matching item for the given 'IngredientId'
        # For example, you can assign a default value or leave it unchanged.
        # Items_Nonstd.loc[index, 'Description'] = 'Not Found'
        pass



In [48]:
Items_Nonstd.head()

IngredientId   Qty  Uom  Conversion  InvFactor   Recipe  \
0      I-13327  0.75  pak         1.0     0.0125  P-12392   
1       I-2501  0.25  pak         1.0     0.0042  P-12392   
2      I-17680  0.20  bag         1.0     0.0333  P-14076   
4      I-19633  1.00  pak         1.0     0.3333  P-23837   
5      I-17151  5.00   CT         1.0     0.5000  P-28369   

                      Description  
0           COFFEE LUSH 42 X 110G  
1          COFFEE SUPER DARK 110g  
2  CEREAL CORNPUFF GORILA MNCH GF  
4              YOGURT FROZEN MIX   
5         CIABATTA TUSCANO SLICED

In [49]:
# Convert the Items_Nonstd DataFrame to a csv file
path = os.path.join(os.getcwd(), "data", "cleaning", "Items_Nonstd.csv")
Items_Nonstd.to_csv(path, index = False, header = True)

***
## Clean Preps Units

In [50]:
Preps

PrepId                     Description    PakQty PakUOM  \
0     P-61901              ADD|Gomae|broccoli   120.000      g   
1     P-57304    ADD|Pasta accoutresmonts| +2   150.000      g   
2     P-47540                   Alfredo- 2018    15.000      L   
3     P-46066              Almond Milk Yeild    900.000     ml   
4     P-49557             ALMOND UNSALTED CUP     1.000    cup   
5      P-8814       Aoli- RoastedGarlic Thyme     1.100      L   
6     P-49605                    APPLE|Cubed     75.000      g   
7     P-46871                Arancini- dredge     1.500     Kg   
8     P-26184                     BAKED|Beans     9.000     Kg   
9     P-55682                  BAKED|Beans|FF    10.000     Kg   
10    P-54666     BAKED|Pasta|Chicken Alfredo     6.176     Kg   
11    P-54664       BAKED|Pasta|Chorizo Penne     7.360     Kg   
12    P-48759             BANANA CHIP CUP G&G     1.000    cup   
13    P-70055          BASIC|Egg Omelette|AAD     1.000   each   
14    P-44724         BASIC|Omelett|Egg White     1.000   each   
15    P-41321          BATCH| Fish Batter 2.0     1.200      L   
16    P-27317    BATCH|3 Bean Vegetable Chili    21.000     Kg   
17    P-26682  BATCH|Black/White Sesame Seeds   907.186      g   
18    P-68381        BATCH|Brocco Wings|Baked     1.000     Kg   
19    P-56699   BATCH|Cauliflower Wings|Baked     1.000     Kg   
20    P-55945               BATCH|Chaat Salad     1.500     Kg   
21    P-64163      Batch|Chicken Burger|Shoyu     7.650     Kg   
22    P-68227         BATCH|Chickpea Vindaloo     1.200     Kg   
23    P-26333         BATCH|Citrus Herb Aioli     3.000      L   
24    P-53598              BATCH|Coleslaw mix     1.500     Kg   
25    P-56629            BATCH|Corn Succotash     2.700     Kg   
26    P-56398                 BATCH|Guacamole     4.500     Kg   
27    P-44643             BATCH|Hashbrown|GRL     2.000     Kg   
28    P-26075    BATCH|Jalapeno Cilantro Slaw     5.000     Kg   
29    P-56427           BATCH|Olive Tapenade    350.000      g   
30    P-58350     BATCH|Pumpkin Coconut Sauce     5.000      L   
31    P-43729       BATCH|Shoyu Chicken Thigh     7.650     Kg   
32    P-56698              BATCH|Tofu Lardons     1.000     Kg   
33    P-56763     BATCH|Vegan Blanco sauce|MC     0.750      L   
34    P-69680            BATCH|ZucStick|Baked     1.000     Kg   
35    P-56700        BATTER|Cauliflower Wings     1.000      L   
36    P-15353                  BATTER|Tempura     5.000      L   
37    P-44752       BBQ Farmers lunch chicken   120.000      g   
38    P-47328                     BBQ|salmon    140.000    PTN   
39    P-47705         BC Mushroom Quinoa Bowl     1.000   each   
40    P-29190          Bean-Mixed Ragout Prep    15.000     Kg   
41    P-45097             Beans-GarbanzoYeild     1.900     Kg   
42     P-7636              Beans-Kidney Yeild     1.900     Kg   
43    P-37867               Beans-Romano Prep     5.000     Kg   
44    P-49155  BEEF|SHVD inside round|Pho|FLX     6.000     Kg   
45    P-22761            BEV|Juice Bulk|Apple    18.620      L   
46    P-22764           BEV|Juice Bulk|Orange    15.960      L   
47    P-22768          BEV|Pop|Bulk|Coke Diet   120.000      L   
48    P-62687          BEV|Pop|Bulk|Coke Zero    60.000      L   
49    P-64865            big chicken wing|GRL     9.900     Kg   
50    P-52941  BISQUE|Coconut| taco Prawn|FLX     0.500      L   
51    P-49760        BLANCHED|Sprouts Spinach     0.200     Kg   
52    P-61843    BNO|Burrito Vegetables|VEGAN     0.500     Kg   
53    P-26047      BOILED|Hard Boiled Eggs FT    50.000     ea   
54    P-49607    BONES|Halibut|Bouillabaisse     35.000      L   
55    P-61995   BOUQETGARNIS|bay rosmur thyme   600.000      g   
56    P-53001   BOUQETGARNIS|lemongrass thyme   600.000      g   
57    P-50473         BRAISED|Beef Short Ribs     8.500     Kg   
58    P-44691                 BRAISED|cabbage     9.500     Kg   
59    P-13890                 Bread for toast  

In [51]:
pd.read_csv("data/cleaning/update/Preps_UpdateUom.csv")

PrepId                     Description  PakQty   PakUOM  \
0    P-54697                 LEMON|Wedge 1/8    8.00     each   
1    P-35132      MARINATED|Lemon & Herb Chx  185.00       ea   
2    P-51992       YIELD|Bread|Sourdough 5/8   36.00    slice   
3    P-26234      BATCH|Roasted Garlic Bread   16.00       ea   
4    P-26170               GRILLED|NaanBread    1.00       ea   
5    P-16305              YIELD|Smokie (1pc)    1.00       ea   
6    P-26047      BOILED|Hard Boiled Eggs FT   50.00       ea   
7    P-26631      BRK|Pancake|Chocolate Chip   24.00       ea   
8    P-26057        FRIED|Sunny/Overeasy Egg    1.00       ea   
9    P-26056                  GRILLED|Tomato    1.00       ea   
10   P-44587                   GRL|FRIED|Egg    1.00       ea   
11   P-26481                POACHED|Egg|Soft    1.00       ea   
12   P-52620         GARNISH|Lime Mini Wedge    8.00    piece   
13   P-51510            SLICED|Avocado|1/4ea    4.00      PTN   
14   P-50398                 STICKS|Cucumber   12.00       CT   
15   P-61796         MARINADE|Bali Pork Chop   10.00       CT   
16   P-35713               BLACKENED|Chicken  185.00       ea   
17   P-51508              COOKED|Bacon|Slice    2.00    slice   
18   P-56795               COOKED|Burger 4oz    1.00       ea   
19   P-50809        YIELD|Country Loaf|Slice   18.00    slice   
20   P-50439                   FRIED|Tostada    3.00    piece   
21   P-57631           SKEWER|Greek Chicken     1.00     each   
22   P-26318                BAKEDPuff Pastry   10.00       ea   
23   P-61769          STEW|Chicken Pot Pie      8.00      PIE   
24   P-55238      MARINADE|Peri Peri Chicken  120.00       ea   
25   P-43635     ROASTED|Thai Chicken Thighs   25.00       ea   
26   P-37297              COOKED|Poached Egg    1.00     each   
27   P-53056          GRILLED|Roma Tomato|V2   13.00      PTN   
28   P-52222    YIELD|Pickle Spear ea 20-30g    1.00       ea   
29   P-26965        BAKED|Jalapeno Cornbread   12.00    piece   
30   P-28369                      COST|Bread    1.00       ea   
31   P-28372                    COST|Cheeses    1.00    slice   
32   P-28373                 COST|Vegetables    1.00       un   
33   P-52942          FILLING|Taco|Prawn|FLX    1.00     each   
34   P-51230           WINGS|Sauce Mix|ratio    1.00     srvg   
35   P-45255            YIELD|Chicken Strips   70.00    piece   
36   P-52994                YIELD|Prawn|TACO   35.00     each   
37   P-44392               PREP|Eggs|poached    8.00     each   
38   P-44506          SLICED|Avocado|Quarter    4.00     each   
39   P-43737             VEG|Soft Boiled Egg   20.00     each   
40   P-51826       GARNISH|Fried Rice Friday    1.00      PTN   
41   P-61508            GRILLED|Mexican Corn    8.00       ea   
42   P-46509               YIELD|Lettuce bun    3.00      PTN   
43    P-5548                    PREP|Lasagna    3.00  full in   
44    P-5960                   PREP|Tiramisu    1.00  full in   
45   P-61646              PREP|Chicken Wings  100.00       ea   
46   P-60970           SAND|IItalian Grander    1.00     each   
47   P-54644                  BAKED|Moussaka   16.00      PTN   
48   P-54667     BAKED|Pasta|Bolognese Penne   16.00      PTN   
49   P-53088      BATCH|Enchiladas Vegan|POP    6.00     each   
50   P-41727      BATCH|Lentil & Squash Stew   15.00      PTN   
51   P-62403           BATCH|RELLENO|Poblano    1.00     each   
52   P-53361           Batter|Pancake|Banana   24.00       ea   
53   P-51518        COOKED|4 oz Burger Patty    1.00      PTN   
54   P-55099        COOKED|6 oz Burger Patty    1.00      PTN   
55   P-47324         COOKED|Meatball Blended  180.00     each   
56   P-48863          DES|Brown Rice Pudding   12.00       CT   
57   P-51018          DOUGH|BreakfastBiscuit    5.00     each   
58   P-55422      FILLING|ChocCheeseCake|G&G    2.50       1L   
59   P-44353              FLEX|Savoury Chaat    7.00      PTN   
60   P-47610        FLEXlCyprus Mannoush 

In [52]:
# Creates 2 new columns called StdQty and StdUom in the Preps DataFrame. These columns contain NaN values
# Preparing to fill in these columns with standardized quantities and units of measurement 
Preps['StdQty'] = np.nan
Preps['StdUom'] = np.nan

In [53]:
# Convert uom into 'g' or 'ml' for each prep using the unit converter

# Retrieve the PrepId, PakQty, and PakUOM from the current row
# Pass these values to spc_converter, then we update the StdQty and StdUom columns of the current row with the converted values.
for index in Preps.index:
    PrepId = Preps.loc[index,'PrepId']
    Qty = Preps.loc[index,'PakQty']
    Uom = Preps.loc[index,'PakUOM']
    Preps.loc[index,'StdQty'] = spc_converter(PrepId, Qty, Uom)[0]
    Preps.loc[index,'StdUom'] = spc_converter(PrepId, Qty, Uom)[1]

In [54]:
Preps

PrepId                     Description    PakQty PakUOM  \
0     P-61901              ADD|Gomae|broccoli   120.000      g   
1     P-57304    ADD|Pasta accoutresmonts| +2   150.000      g   
2     P-47540                   Alfredo- 2018    15.000      L   
3     P-46066              Almond Milk Yeild    900.000     ml   
4     P-49557             ALMOND UNSALTED CUP     1.000    cup   
5      P-8814       Aoli- RoastedGarlic Thyme     1.100      L   
6     P-49605                    APPLE|Cubed     75.000      g   
7     P-46871                Arancini- dredge     1.500     Kg   
8     P-26184                     BAKED|Beans     9.000     Kg   
9     P-55682                  BAKED|Beans|FF    10.000     Kg   
10    P-54666     BAKED|Pasta|Chicken Alfredo     6.176     Kg   
11    P-54664       BAKED|Pasta|Chorizo Penne     7.360     Kg   
12    P-48759             BANANA CHIP CUP G&G     1.000    cup   
13    P-70055          BASIC|Egg Omelette|AAD     1.000   each   
14    P-44724         BASIC|Omelett|Egg White     1.000   each   
15    P-41321          BATCH| Fish Batter 2.0     1.200      L   
16    P-27317    BATCH|3 Bean Vegetable Chili    21.000     Kg   
17    P-26682  BATCH|Black/White Sesame Seeds   907.186      g   
18    P-68381        BATCH|Brocco Wings|Baked     1.000     Kg   
19    P-56699   BATCH|Cauliflower Wings|Baked     1.000     Kg   
20    P-55945               BATCH|Chaat Salad     1.500     Kg   
21    P-64163      Batch|Chicken Burger|Shoyu     7.650     Kg   
22    P-68227         BATCH|Chickpea Vindaloo     1.200     Kg   
23    P-26333         BATCH|Citrus Herb Aioli     3.000      L   
24    P-53598              BATCH|Coleslaw mix     1.500     Kg   
25    P-56629            BATCH|Corn Succotash     2.700     Kg   
26    P-56398                 BATCH|Guacamole     4.500     Kg   
27    P-44643             BATCH|Hashbrown|GRL     2.000     Kg   
28    P-26075    BATCH|Jalapeno Cilantro Slaw     5.000     Kg   
29    P-56427           BATCH|Olive Tapenade    350.000      g   
30    P-58350     BATCH|Pumpkin Coconut Sauce     5.000      L   
31    P-43729       BATCH|Shoyu Chicken Thigh     7.650     Kg   
32    P-56698              BATCH|Tofu Lardons     1.000     Kg   
33    P-56763     BATCH|Vegan Blanco sauce|MC     0.750      L   
34    P-69680            BATCH|ZucStick|Baked     1.000     Kg   
35    P-56700        BATTER|Cauliflower Wings     1.000      L   
36    P-15353                  BATTER|Tempura     5.000      L   
37    P-44752       BBQ Farmers lunch chicken   120.000      g   
38    P-47328                     BBQ|salmon    140.000    PTN   
39    P-47705         BC Mushroom Quinoa Bowl     1.000   each   
40    P-29190          Bean-Mixed Ragout Prep    15.000     Kg   
41    P-45097             Beans-GarbanzoYeild     1.900     Kg   
42     P-7636              Beans-Kidney Yeild     1.900     Kg   
43    P-37867               Beans-Romano Prep     5.000     Kg   
44    P-49155  BEEF|SHVD inside round|Pho|FLX     6.000     Kg   
45    P-22761            BEV|Juice Bulk|Apple    18.620      L   
46    P-22764           BEV|Juice Bulk|Orange    15.960      L   
47    P-22768          BEV|Pop|Bulk|Coke Diet   120.000      L   
48    P-62687          BEV|Pop|Bulk|Coke Zero    60.000      L   
49    P-64865            big chicken wing|GRL     9.900     Kg   
50    P-52941  BISQUE|Coconut| taco Prawn|FLX     0.500      L   
51    P-49760        BLANCHED|Sprouts Spinach     0.200     Kg   
52    P-61843    BNO|Burrito Vegetables|VEGAN     0.500     Kg   
53    P-26047      BOILED|Hard Boiled Eggs FT    50.000     ea   
54    P-49607    BONES|Halibut|Bouillabaisse     35.000      L   
55    P-61995   BOUQETGARNIS|bay rosmur thyme   600.000      g   
56    P-53001   BOUQETGARNIS|lemongrass thyme   600.000      g   
57    P-50473         BRAISED|Beef Short Ribs     8.500     Kg   
58    P-44691                 BRAISED|cabbage     9.500     Kg   
59    P-13890                 Bread for toast  

In [55]:
# Save cleaned preps list to file
path = os.path.join(os.getcwd(), "data", "cleaning", "Preps_Unit_Cleaned.csv")
Preps.to_csv(path, index = False, header = True)

In [56]:
pd.read_csv("data/cleaning/update/Preps_UpdateUom.csv")

PrepId                     Description  PakQty   PakUOM  \
0    P-54697                 LEMON|Wedge 1/8    8.00     each   
1    P-35132      MARINATED|Lemon & Herb Chx  185.00       ea   
2    P-51992       YIELD|Bread|Sourdough 5/8   36.00    slice   
3    P-26234      BATCH|Roasted Garlic Bread   16.00       ea   
4    P-26170               GRILLED|NaanBread    1.00       ea   
5    P-16305              YIELD|Smokie (1pc)    1.00       ea   
6    P-26047      BOILED|Hard Boiled Eggs FT   50.00       ea   
7    P-26631      BRK|Pancake|Chocolate Chip   24.00       ea   
8    P-26057        FRIED|Sunny/Overeasy Egg    1.00       ea   
9    P-26056                  GRILLED|Tomato    1.00       ea   
10   P-44587                   GRL|FRIED|Egg    1.00       ea   
11   P-26481                POACHED|Egg|Soft    1.00       ea   
12   P-52620         GARNISH|Lime Mini Wedge    8.00    piece   
13   P-51510            SLICED|Avocado|1/4ea    4.00      PTN   
14   P-50398                 STICKS|Cucumber   12.00       CT   
15   P-61796         MARINADE|Bali Pork Chop   10.00       CT   
16   P-35713               BLACKENED|Chicken  185.00       ea   
17   P-51508              COOKED|Bacon|Slice    2.00    slice   
18   P-56795               COOKED|Burger 4oz    1.00       ea   
19   P-50809        YIELD|Country Loaf|Slice   18.00    slice   
20   P-50439                   FRIED|Tostada    3.00    piece   
21   P-57631           SKEWER|Greek Chicken     1.00     each   
22   P-26318                BAKEDPuff Pastry   10.00       ea   
23   P-61769          STEW|Chicken Pot Pie      8.00      PIE   
24   P-55238      MARINADE|Peri Peri Chicken  120.00       ea   
25   P-43635     ROASTED|Thai Chicken Thighs   25.00       ea   
26   P-37297              COOKED|Poached Egg    1.00     each   
27   P-53056          GRILLED|Roma Tomato|V2   13.00      PTN   
28   P-52222    YIELD|Pickle Spear ea 20-30g    1.00       ea   
29   P-26965        BAKED|Jalapeno Cornbread   12.00    piece   
30   P-28369                      COST|Bread    1.00       ea   
31   P-28372                    COST|Cheeses    1.00    slice   
32   P-28373                 COST|Vegetables    1.00       un   
33   P-52942          FILLING|Taco|Prawn|FLX    1.00     each   
34   P-51230           WINGS|Sauce Mix|ratio    1.00     srvg   
35   P-45255            YIELD|Chicken Strips   70.00    piece   
36   P-52994                YIELD|Prawn|TACO   35.00     each   
37   P-44392               PREP|Eggs|poached    8.00     each   
38   P-44506          SLICED|Avocado|Quarter    4.00     each   
39   P-43737             VEG|Soft Boiled Egg   20.00     each   
40   P-51826       GARNISH|Fried Rice Friday    1.00      PTN   
41   P-61508            GRILLED|Mexican Corn    8.00       ea   
42   P-46509               YIELD|Lettuce bun    3.00      PTN   
43    P-5548                    PREP|Lasagna    3.00  full in   
44    P-5960                   PREP|Tiramisu    1.00  full in   
45   P-61646              PREP|Chicken Wings  100.00       ea   
46   P-60970           SAND|IItalian Grander    1.00     each   
47   P-54644                  BAKED|Moussaka   16.00      PTN   
48   P-54667     BAKED|Pasta|Bolognese Penne   16.00      PTN   
49   P-53088      BATCH|Enchiladas Vegan|POP    6.00     each   
50   P-41727      BATCH|Lentil & Squash Stew   15.00      PTN   
51   P-62403           BATCH|RELLENO|Poblano    1.00     each   
52   P-53361           Batter|Pancake|Banana   24.00       ea   
53   P-51518        COOKED|4 oz Burger Patty    1.00      PTN   
54   P-55099        COOKED|6 oz Burger Patty    1.00      PTN   
55   P-47324         COOKED|Meatball Blended  180.00     each   
56   P-48863          DES|Brown Rice Pudding   12.00       CT   
57   P-51018          DOUGH|BreakfastBiscuit    5.00     each   
58   P-55422      FILLING|ChocCheeseCake|G&G    2.50       1L   
59   P-44353              FLEX|Savoury Chaat    7.00      PTN   
60   P-47610        FLEXlCyprus Mannoush 

### Get Preps with Nonstandard Unit

In [57]:
col_names = list(Preps.columns.values)
Preps_Nonstd = []

for index, row in Preps.iterrows():
    StdUom = Preps.loc[index,'StdUom']
    if StdUom not in ['g', 'ml']:
        Dict = {}
        Dict.update(dict(row))
        Preps_Nonstd.append(Dict)

Preps_Nonstd = pd.DataFrame(Preps_Nonstd, columns = col_names)

In [58]:
Preps_Nonstd

PrepId                     Description  PakQty PakUOM  \
0   P-70055          BASIC|Egg Omelette|AAD     1.0   each   
1   P-44724         BASIC|Omelett|Egg White     1.0   each   
2   P-47328                     BBQ|salmon    140.0    PTN   
3   P-47705         BC Mushroom Quinoa Bowl     1.0   each   
4   P-46861     Buns- toasted po-boy slider    12.0   each   
5   P-46644       BVSTO - Fire Roasted Corn    96.0    PTN   
6   P-46643    BVSTO|Salmon (Brined&Smoked)    50.0    PTN   
7   P-40627       Caliente-Quinoa Enchilada    15.0    PTN   
8   P-14135     Cheese White Cheddar Sliced     2.0  slice   
9    P-7137         COOKED|Drumsticks Halal   350.0  piece   
10  P-36899           COOKED|kuttera rst|SL    10.0     ea   
11  P-70984   COOKED|Pate brisee pastry lid    24.0     ea   
12  P-50773          COOKED|Pork chop Cajun    12.0     CT   
13  P-22963               COOKED|waffle|FNH     1.0     ea   
14  P-40886   Delish-Vegan Chocolate Mousse    10.0    PTN   
15  P-69721           DES|Bar|Apple Crumble     1.0  slice   
16  P-69723                 DES|Cake|Carrot     1.0  slice   
17  P-69719       DES|Cake|German Chocolate     1.0  slice   
18  P-69720            DES|Cake|Maple Mania     1.0  slice   
19  P-52950        DESSERT|Baked Yogurt|BBC    15.0   each   
20  P-13019      FF-Cornbread Jalapeno Ched    24.0     ea   
21  P-39031    FF|Bowl|Thai Coconut DONTUSE     1.0    PTN   
22  P-53784          FNH|apple crumble|EACH     6.0   each   
23  P-53606                G&G|Ed Peach Pie     1.0    PIE   
24  P-54796     G&G|Mini Choc Cake|Uncle Ed    70.0   each   
25  P-64432    G&G|Nutella Brownie|Uncle Ed    24.0   each   
26  P-53370          G&G|Uncle Ed Apple Pie     1.0    PIE   
27  P-53379   G&G|Uncle Ed Apple Rhub Crisp     1.0  SHEET   
28  P-53804           G&G|Uncle Ed's BC Pie    12.0  piece   
29  P-26170               GRILLED|NaanBread     1.0    PTN   
30  P-47966  Gyaza-Sushi Avocado Roll (12pc     1.0    pak   
31  P-46069      HCMG-Bnna Almnd Buttr Bulk    40.0   each   
32  P-46075     HCMG-Breakfast Yorkies Prep    30.0   each   
33  P-46072       HCMG-Chutney-Apple Raisin    24.0    PTN   
34  P-46080                HCMG-Fruit Salad    33.0    PTN   
35  P-46071     HCMG-Pancakes-Oat and Apple    30.0   each   
36  P-44386              Moroccan lamb stew    80.0    PTN   
37  P-28341            OK - Corn on the Cob    96.0   each   
38  P-44727       Omelette- Whole Egg-Basic     1.0   each   
39  P-47051         Pop-up Oyster pan fried     3.0   each   
40  P-46877        Pop-up- Oysters- Breaded    12.0     ea   
41  P-66125             POP|Veg Empanada|Ed     1.0     CT   
42   P-7637           PREP Sour Cream/Salsa     1.0   srvg   
43  P-56612    PREP|Almonds are forever|TST     2.0     ea   
44  P-50612             PREP|Apple Brine|SL     1.5     1L   
45  P-46947             PREP|Arancini balls     1.0   each   
46  P-56119         PREP|Bread Pudding|SPEC    22.0  slice   
47  P-50505      PREP|Buttermilk Pancakes|2     2.0   each   
48  P-65742            PREP|Potstickers (3)     1.0   each   
49  P-51225            PREP|Skewer Yakitori     2.0     ea   
50  P-32151         PREP|Sliced Roma Tomato    20.0  slice   
51  P-43638  PREP|smoothie|BananaMatcha|AAD     2.0     ea   
52  P-43637    PREP|smoothie|Blue Boost|AAD     4.0     ea   
53  P-55184           PREP|Smoothie|C++|AAD     4.0     ea   
54  P-36780   PREP|smoothie|Chocohiolic|AAD     2.0     ea   
55  P-36815        PREP|smoothie|Delish|AAD     4.0     ea   
56  P-56681  PREP|smoothie|Greenmeansgo|AAD     2.0     ea   
57  P-50627        PREP|smoothie|Nojito|AAD     2.0   srvg   
58  P-36066    PREP|smoothie|Rise&Shine|AAD     4.0     ea   
59  P-70079                PREP|Spanish pie    12.0  piece   
60  P-50646                  SAND|Panini|SP     1.0     un   
61  P-55574          SAUCE|Blue cheese|SPEC   100.0     CT   
62  P-38127                   SCONE ASST CK     1.0     ea   
63  P-47776         SMOOTHIE|Apple Ci

In [59]:
# Filter out preps with nonstandard uom but have information already
Manual_PrepU = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "update", "Preps_UpdateUom.csv"))

col_names = list(Preps_Nonstd.columns.values)
Preps_Nonstd_na = []

for index, row in Preps_Nonstd.iterrows():
    PrepId = Preps_Nonstd.loc[index,'PrepId']
    if PrepId not in Manual_PrepU['PrepId'].values:
        Dict = {}
        Dict.update(dict(row))
        Preps_Nonstd_na.append(Dict)

Preps_Nonstd = pd.DataFrame(Preps_Nonstd_na, columns = col_names)
Preps_Nonstd

Empty DataFrame
Columns: [PrepId, Description, PakQty, PakUOM, InventoryGroup, StdQty, StdUom]
Index: []

In [60]:
path = os.path.join(os.getcwd(), "data", "cleaning", "Preps_NonstdUom.csv")
Preps_Nonstd.to_csv(path, index = False, header = True)

In [61]:
update_prep = pd.read_csv("data/cleaning/update/Preps_UpdateUom.csv")
update_prep

PrepId                     Description  PakQty   PakUOM  \
0    P-54697                 LEMON|Wedge 1/8    8.00     each   
1    P-35132      MARINATED|Lemon & Herb Chx  185.00       ea   
2    P-51992       YIELD|Bread|Sourdough 5/8   36.00    slice   
3    P-26234      BATCH|Roasted Garlic Bread   16.00       ea   
4    P-26170               GRILLED|NaanBread    1.00       ea   
5    P-16305              YIELD|Smokie (1pc)    1.00       ea   
6    P-26047      BOILED|Hard Boiled Eggs FT   50.00       ea   
7    P-26631      BRK|Pancake|Chocolate Chip   24.00       ea   
8    P-26057        FRIED|Sunny/Overeasy Egg    1.00       ea   
9    P-26056                  GRILLED|Tomato    1.00       ea   
10   P-44587                   GRL|FRIED|Egg    1.00       ea   
11   P-26481                POACHED|Egg|Soft    1.00       ea   
12   P-52620         GARNISH|Lime Mini Wedge    8.00    piece   
13   P-51510            SLICED|Avocado|1/4ea    4.00      PTN   
14   P-50398                 STICKS|Cucumber   12.00       CT   
15   P-61796         MARINADE|Bali Pork Chop   10.00       CT   
16   P-35713               BLACKENED|Chicken  185.00       ea   
17   P-51508              COOKED|Bacon|Slice    2.00    slice   
18   P-56795               COOKED|Burger 4oz    1.00       ea   
19   P-50809        YIELD|Country Loaf|Slice   18.00    slice   
20   P-50439                   FRIED|Tostada    3.00    piece   
21   P-57631           SKEWER|Greek Chicken     1.00     each   
22   P-26318                BAKEDPuff Pastry   10.00       ea   
23   P-61769          STEW|Chicken Pot Pie      8.00      PIE   
24   P-55238      MARINADE|Peri Peri Chicken  120.00       ea   
25   P-43635     ROASTED|Thai Chicken Thighs   25.00       ea   
26   P-37297              COOKED|Poached Egg    1.00     each   
27   P-53056          GRILLED|Roma Tomato|V2   13.00      PTN   
28   P-52222    YIELD|Pickle Spear ea 20-30g    1.00       ea   
29   P-26965        BAKED|Jalapeno Cornbread   12.00    piece   
30   P-28369                      COST|Bread    1.00       ea   
31   P-28372                    COST|Cheeses    1.00    slice   
32   P-28373                 COST|Vegetables    1.00       un   
33   P-52942          FILLING|Taco|Prawn|FLX    1.00     each   
34   P-51230           WINGS|Sauce Mix|ratio    1.00     srvg   
35   P-45255            YIELD|Chicken Strips   70.00    piece   
36   P-52994                YIELD|Prawn|TACO   35.00     each   
37   P-44392               PREP|Eggs|poached    8.00     each   
38   P-44506          SLICED|Avocado|Quarter    4.00     each   
39   P-43737             VEG|Soft Boiled Egg   20.00     each   
40   P-51826       GARNISH|Fried Rice Friday    1.00      PTN   
41   P-61508            GRILLED|Mexican Corn    8.00       ea   
42   P-46509               YIELD|Lettuce bun    3.00      PTN   
43    P-5548                    PREP|Lasagna    3.00  full in   
44    P-5960                   PREP|Tiramisu    1.00  full in   
45   P-61646              PREP|Chicken Wings  100.00       ea   
46   P-60970           SAND|IItalian Grander    1.00     each   
47   P-54644                  BAKED|Moussaka   16.00      PTN   
48   P-54667     BAKED|Pasta|Bolognese Penne   16.00      PTN   
49   P-53088      BATCH|Enchiladas Vegan|POP    6.00     each   
50   P-41727      BATCH|Lentil & Squash Stew   15.00      PTN   
51   P-62403           BATCH|RELLENO|Poblano    1.00     each   
52   P-53361           Batter|Pancake|Banana   24.00       ea   
53   P-51518        COOKED|4 oz Burger Patty    1.00      PTN   
54   P-55099        COOKED|6 oz Burger Patty    1.00      PTN   
55   P-47324         COOKED|Meatball Blended  180.00     each   
56   P-48863          DES|Brown Rice Pudding   12.00       CT   
57   P-51018          DOUGH|BreakfastBiscuit    5.00     each   
58   P-55422      FILLING|ChocCheeseCake|G&G    2.50       1L   
59   P-44353              FLEX|Savoury Chaat    7.00      PTN   
60   P-47610        FLEXlCyprus Mannoush 

***

## New Items

In [62]:
# Load current Items List with assigned Emission Factors Category ID
Items_Assigned = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "Items_List_Assigned.csv"))
Items_Assigned.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545         1.0   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869         1.0       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064         1.0     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005         1.0            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002         1.0  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

In [63]:
Items_Assigned.shape

(2821, 8)

In [64]:
Items_Assigned["InventoryGroup"].unique()

array(['MEAT', 'DELI & PREPARED MEAT', 'FOOD - GROCERY', 'POULTRY',
       'PRODUCTION FOOD', 'DAIRY', 'BAKING-RAW INGREDIENTS', 'PRODUCE',
       'ICECREAM/NOVELTY/GELATO', 'SEAFOOD', 'CANDIES SNACKS', 'MISC.',
       'MM Grocery Cereal', 'BAKED GOODS', 'MM Grocery Chill', 'PREP',
       'BREAD', 'MM BAKERY', 'ZDONT USE FOOD', 'SPICES', 'FAIR TRADE',
       'MM Snack Ethnic', 'HM FROZEN SINGLE SERVE',
       'CHIPS, PRETZELS, NUTS', 'ZDONT USE FROZEN', 'BEVERAGE',
       'PACKAGED BEER, CIDER', 'LIQUOR', 'ALCOHOL - FOOD',
       'MM CANDY Chocolate ', 'PREGEL - ALL ITEMS',
       'HM SWEET & SAVOURY SNACKS', 'UCARE',
       'HM CHILL SINGLE SERVE BEVERAGE', 'JERKY, PEPPERONI', 'SUSHI',
       'MM CANDY Bulk', 'MM CANDY Gum & Mints', 'MM Snack Single Bars',
       'MERCHANDISE', 'MM Frozen Grocery', 'MM Frozen HMR', 'MM Grocery',
       'MM Grocery Coffee & Tea', 'MM Grocery Ethnic', 'MM Grocery Soup',
       'MM MERCH OTC', 'MM Snack Jerky', 'ZDONT USE CANDY - GUM & MINTS',
       'DI

In [65]:
Items_Assigned["CategoryID"].unique()

array([ 1.,  2.,  3.,  4.,  5.,  6.,  7.,  8.,  9., 10., 11., 12., 13.,
       14., 16., 17., 18., 19., 20., 21., 22., 23., 24., 25., 26., 27.,
       28., 30., 31., 32., 33., 34., 35., 36., 37., 38., 39., 40., 41.,
       42., 43., 44., 48., 49., 50., 51., 52., 53., 54., 55., 56., 57.,
       58., 59., 60., 61.])

In [66]:
Items_Assigned[Items_Assigned["CategoryID"] == 55]

ItemId  CategoryID                     Description  CaseQty  CaseUOM  \
1287  I-11794        55.0    YERBA MATE REVEL BERRY 458ML     12.0     each   
1288   I-1683        55.0         WATER VITAMIN ZERO XOXO     12.0    591ML   
1289   I-2955        55.0      WATER SPARKLING SAN PELLEG     24.0      PTN   
1290  I-52773        55.0    WATER SMART SPARKLING RASPB      12.0     each   
1291   I-5983        55.0               WATER FOR RECIPES      1.0        L   
1292  I-11671        55.0    WATER DASANI SPARKLING LEMON     12.0    355ML   
1293   I-1644        55.0              WATER DASANI 591ML     24.0    591ML   
1294  I-13982        55.0  TEA CHAI BOULDER CONCENT 3RDST      1.0      JUG   
1295  I-37651        55.0             TEA BLACK EARL GREY      6.0      box   
1296   I-1598        55.0         SODA SAN PELL LIMONATA      24.0    355ML   
1297   I-1590        55.0       SODA SAN PELL ARANCIATTA      24.0    355ML   
1298  I-11159        55.0        ODWALLA STRAW BANA 450ml      8.0     each   
1299  I-11158        55.0       ODWALLA MANGO TANGO 450ml      8.0       ea   
1300   I-1750        55.0       ODWALLA LIFEFOOD ORIGINAL      8.0    450ML   
1301   I-1821        55.0           JUICE PINEAPPLE TETRA     12.0   bottle   
1302  I-41738        55.0        JUICE PEACH SIMPLY 340ml     12.0     each   
1303   I-1820        55.0  JUICE ORANGE UNSWEETENED TETRA     12.0        L   
1304  I-13968        55.0      JUICE ORANGE SIMPLY  340ML     12.0       ea   
1305  I-43253        55.0           JUICE ORANGE MM 355ML     12.0    355ML   
1306  I-13967        55.0  JUICE LEMONADE SIMPLY RASPBERY     12.0    340ML   
1307  I-56154        55.0     JUICE LEMONADE SIMPLY 340ML     12.0    340ML   
1308   I-1690        55.0         JUICE LEMONADE MM 355ML     12.0    355ML   
1309  I-43255        55.0        JUICE CRAN MM CKTL 355ML     12.0    355ML   
1310  I-13969        55.0       JUICE APPLE SIMPLY  340ML      1.0    340ML   
1311   I-1686        55.0             JUICE APPLE MM 450M     24.0    450ML   
1312  I-43252        55.0            JUICE APPLE MM 355ML     12.0    355ML   
1313   I-1687        55.0            JUICE APPLE MM 341ML     12.0    341ML   
1314  I-43254        55.0             JUICE 5 ALIVE 355ML     12.0      can   
1315  I-46622        55.0         ICE TEA UNSWT GOLD PEAK     12.0       ea   
1316  I-46621        55.0         ICE TEA LEMON GOLD PEAK     12.0       ea   
1317  I-46620        55.0           ICE TEA GRN GOLD PEAK     12.0       ea   
1318   I-1642        55.0            COKE CLASSIC BIB 20L      1.0  BIB 20L   
1319   I-1639        55.0              COKE CLASSIC 500ML     24.0    500ML   
1320  I-56025        55.0  AHA WATER SP WATERMLN LIME PET     24.0     each   
1321  I-57484        55.0  AHA WATER SP PEACH HONEY PET       24.0     each   
1322  I-57285        55.0  AHA WATER BLUBRY POM SPARKLING     12.0     each   
1323  I-46554        55.0           MILK COCONUT ORIGINAL     12.0     each   
1324   I-3738        55.0       WATER COCONUT BLUE MONKEY     24.0    330ML   
1325  I-11672        55.0     WATER DASANI SPARKLING LIME     12.0   bottle   
1326  I-11673        55.0     WATER DASANI SPARKLING BERY     12.0    355ML   
1327   I-1634        55.0                 COKE ZERO 500ML     24.0    500ML   
1328   I-1674        55.0             WATER VITAMIN ESNTL     12.0    591ML   
1329   I-1775        55.0            HOT CHOC INSTANT PTN    300.0      PTN   
1330   I-1779        55.0           HOT CHOC LT INST PORT    300.0      pak   
1331   I-1792        55.0        JUICE APPLE CONC 6+1 TFC      4.0      JUG   
1332   I-1814        55.0       JUICE REALEMON PLAS 945ML     12.0    945ML   
1333   I-1816        55.0       JUICE ORANGE CONC 5+1 TFC      4.0      JUG   
1334   I-1827        55.0                JUICE TOMATO CAN      6.0   LG CAN   
1335   I-1863        55.0                     STEAZ PEACH     12.0    473ML   
1336   I-1865        55.0   STEAZ ZERO CAL CITRUS ICD TEA

### Get the List of New Items

In [67]:
# Filter new items by itemID that are not in the database and output them in a dataframe
col_names = list(Items.columns.values)
New_Items_List = []

for index, row in Items.iterrows():
    ItemId = Items.loc[index,'ItemId']
    if ItemId not in Items_Assigned['ItemId'].values:
        Dict = {}
        Dict.update(dict(row))
        New_Items_List.append(Dict)

New_Items = pd.DataFrame(New_Items_List, columns = col_names)

In [68]:
New_Items.insert(1, "CategoryID", '')
New_Items

Empty DataFrame
Columns: [ItemId, CategoryID, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [69]:
New_Items.shape

(0, 8)

In [70]:
# Store the list of new items into .csv file
# If New_Items is not empty then we convert it to a csv file. 
if not New_Items.empty:
    path = os.path.join(os.getcwd(), "data", "mapping", "new items", str(datetime.date(datetime.now()))+"_New_Items.csv")
    New_Items.to_csv(path, index = False, header = True)

In [71]:
# file = pd.read_csv("data/mapping/new items/2022-11-01_New_Items.csv")
# file.to_excel("2022-11-01_New_Items.xlsx",index = None, header=True)
if not New_Items.empty:
    file = pd.read_csv("C:/Users/smvan/CFFS-S23/CFFS-22-23/data/mapping/new items/"+ str(datetime.date(datetime.now()))+"_New_Items.csv")
    file.to_excel(str(datetime.date(datetime.now()))+"_New_Items.xlsx",index = None, header=True)

In [72]:
# file2 = pd.read_excel("data/mapping/new items added/New_Items_Added_11.xlsx")
# file2.to_csv("data/mapping/new items added/New_Items_Added_11.csv", index=False)

file2 = pd.read_excel("data/mapping/new items added/New_Items_2023/New_Items_Added_2023_08_01.xlsx")
file2.to_csv("data/mapping/new items added/New_Items_2023/New_Items_Added_2023_08_01.csv", index=False)

***
## Data Summary

In [73]:
datasum = pd.DataFrame([New_Items.shape, Preps_Nonstd.shape, Items_Nonstd.shape],
                       columns = ['count', 'columns'], 
                       index = ['New_Items', 'Preps_Nonstd', 'Items_Nonstd'])
datasum

count  columns
New_Items         0        8
Preps_Nonstd      0        7
Items_Nonstd    468        7

In [74]:
print(New_Items.columns)

Index(['ItemId', 'CategoryID', 'Description', 'CaseQty', 'CaseUOM', 'PakQty',
       'PakUOM', 'InventoryGroup'],
      dtype='object')
